<h1> F`inding the best cluster or location to open a new gym</h1>

In [63]:
#importing necessary libraries

In [64]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


<h3> The queens data has been fetched from new york json file provided into tutorial and has been cleanewd according to needs </h3>

<h3>USING FOURSQUARE API</h3>
CLIENT_ID = 'S4UORRUVU3PZ34YSPM0OFCRHPQV4T4F0BLGGAGLYETP3NGDV' # your Foursquare ID
CLIENT_SECRET = 'MNB4VVRXSHQI2YRQ34MDTFBQUOQ3031G1VI2ILUVGYK0QYIN' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

<h2>Note: I have commented the foursquare code because my limit used to exceed and because of that I had difficulties <br>
    So, I saved the acquired data into a dataframe as shown in csv table. I'm mentioning code because of evaluation process</h2>

In [3]:
a=pd.read_csv('Queens_venues.csv')

In [5]:
a.drop(columns=['Unnamed: 0'],inplace=True)

In [6]:
a.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Astoria              40.768509              -73.915654   
1      Astoria              40.768509              -73.915654   
2      Astoria              40.768509              -73.915654   
3      Astoria              40.768509              -73.915654   
4      Astoria              40.768509              -73.915654   

              Venue  Venue Latitude  Venue Longitude        Venue Category  
0      Favela Grill       40.767348       -73.917897  Brazilian Restaurant  
1    Orange Blossom       40.769856       -73.917012          Gourmet Shop  
2  Titan Foods Inc.       40.769198       -73.919253          Gourmet Shop  
3   CrossFit Queens       40.769404       -73.918977                   Gym  
4      Off The Hook       40.767200       -73.918104    Seafood Restaurant

<h3>CHECKING HOW MANY VALUES WERE RETURNED FOR EACH CITY IN THE DATASET</h3>


In [22]:
a.groupby(["Neighborhood"]).count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                 
Arverne                                  17                      17     17   
Astoria                                 100                     100    100   
Astoria Heights                          14                      14     14   
Auburndale                               21                      21     21   
Bay Terrace                              41                      41     41   
Bayside                                  71                      71     71   
Bayswater                                 3                       3      3   
Beechhurst                               18                      18     18   
Bellaire                                 11                      11     11   
Belle Harbor                             18                      18     18   
Bellerose                                18                      18     18   
Blissville                               17                      17     17   
Breezy Point                              6                       6      6   
Briarwood                                11                      11     11   
Broad Channel                             7                       7      7   
Brookville                                2                       2      2   
Cambria Heights                          12                      12     12   
College Point                            41                      41     41   
Corona                                   17                      17     17   
Douglaston                               24                      24     24   
East Elmhurst                            14                      14     14   
Edgemere                                 14                      14     14   
Elmhurst                                 39                      39     39   
Far Rockaway                             35                      35     35   
Floral Park                               7                       7      7   
Flushing                                 65                      65     65   
Forest Hills                             39                      39     39   
Forest Hills Gardens                     21                      21     21   
Fresh Meadows                            15                      15     15   
Glen Oaks                                20                      20     20   
Glendale                                  4                       4      4   
Hammels                                  18                      18     18   
Hillcrest                                18                      18     18   
Hollis                                   15                      15     15   
Holliswood                                5                       5      5   
Howard Beach                             38                      38     38   
Hunters Point                            74                      74     74   
Jackson Heights                          80                      80     80   
Jamaica Center                           42                      42     42   
Jamaica Estates                           4                       4      4   
Jamaica Hills                            28                      28     28   
Kew Gardens                              47                      47     47   
Kew Gardens Hills                        20                      20     20   
Laurelton                                 7                       7      7   
Lefrak City                              27                      27     27   
Lindenwood                               10                      10     10   
Little Neck                              50                      50     50   
Long Island City                         73                      73     73   
Malba                                     2                       2      2   
Maspeth                                  31 

<h3>UNIQUE CATEGORIES THAT CAN BE CURATED</h3>

In [23]:
print('There are {} uniques categories.'.format(len(a['Venue Category'].unique())))
a['Venue Category'].unique()[:50]

There are 262 uniques categories.


array(['Brazilian Restaurant', 'Gourmet Shop', 'Gym',
       'Seafood Restaurant', 'Martial Arts Dojo',
       'Middle Eastern Restaurant', 'Pub', 'Mexican Restaurant',
       'Dessert Shop', 'Falafel Restaurant', 'Ice Cream Shop',
       'Greek Restaurant', 'Bakery', 'Bagel Shop',
       'Health & Beauty Service', 'Indian Restaurant', 'Diner',
       'Salad Place', 'Thai Restaurant', 'Italian Restaurant', 'Bar',
       'Creperie', 'Food Truck', 'Pizza Place', 'Bubble Tea Shop',
       'Grocery Store', 'Food', 'Vegetarian / Vegan Restaurant',
       'Food & Drink Shop', 'Mediterranean Restaurant',
       'Latin American Restaurant', 'Beer Garden', 'Hookah Bar',
       'Korean Restaurant', 'Cajun / Creole Restaurant', 'BBQ Joint',
       'Souvlaki Shop', 'Deli / Bodega', 'Sandwich Place', 'Cocktail Bar',
       'Juice Bar', 'Gym / Fitness Center', 'Salon / Barbershop', 'Spa',
       'Frozen Yogurt Shop', 'Café', 'Liquor Store', 'Optical Shop',
       'Comfort Food Restaurant', 'Burger J

<h3>CHECKING IF THE RESULT CONTAINS GYM</h3>

In [25]:
"Gym" in a['Venue Category'].unique()

True

<H3>ANALYZING EACH CITY</H3>

In [27]:
kl_onehot = pd.get_dummies(a[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
kl_onehot['city'] = a['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [kl_onehot.columns[-1]] + list(kl_onehot.columns[:-1])
kl_onehot = kl_onehot[fixed_columns]

print(kl_onehot.shape)
kl_onehot.head()

(2148, 263)


city  Accessories Store  Afghan Restaurant  American Restaurant  \
0  Astoria                  0                  0                    0   
1  Astoria                  0                  0                    0   
2  Astoria                  0                  0                    0   
3  Astoria                  0                  0                    0   
4  Astoria                  0                  0                    0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  \
0                   0                0          0           0           0   
1                   0                0          0           0           0   
2                   0                0          0           0           0   
3                   0                0          0           0           0   
4                   0                0          0           0           0   

   Bakery  Bank  Bar  Baseball Field  Basketball Court  Bath House  Beach  \
0       0     0    0               0                 0           0      0   
1       0     0    0               0                 0           0      0   
2       0     0    0               0                 0           0      0   
3       0     0    0               0                 0           0      0   
4       0     0    0               0                 0           0      0   

   Beach Bar  Bed & Breakfast  Beer Garden  Bike Trail  Bistro  Board Shop  \
0          0                0            0           0       0           0   
1          0                0            0           0       0           0   
2          0                0            0           0       0           0   
3          0                0            0           0       0           0   
4          0                0            0           0       0           0   

   Bookstore  Boutique  Bowling Alley  Brazilian Restaurant  Breakfast Spot  \
0          0         0              0                     1               0   
1          0         0              0                     0               0   
2          0         0              0                     0               0   
3          0         0              0                     0               0   
4          0         0              0                     0               0   

   Brewery  Bubble Tea Shop  Buffet  Burger Joint  Burrito Place  Bus Line  \
0        0                0       0             0              0         0   
1        0                0       0             0              0         0   
2        0                0       0             0              0         0   
3        0                0       0             0              0         0   
4        0                0       0             0              0         0   

   Bus Station  Bus Stop  Business Service  Cafeteria  Café  \
0            0         0                 0          0     0   
1            0         0                 0          0     0   
2            0         0                 0          0     0   
3            0         0                 0          0     0   
4            0         0                 0          0     0   

   Cajun / Creole R

<h3>GROUPING THE RESULT</h3>

In [28]:
kl_grouped = kl_onehot.groupby(["city"]).mean().reset_index()

print(kl_grouped.shape)
kl_grouped

(81, 263)


city  Accessories Store  Afghan Restaurant  \
0                Arverne           0.000000           0.000000   
1                Astoria           0.000000           0.000000   
2        Astoria Heights           0.000000           0.000000   
3             Auburndale           0.000000           0.000000   
4            Bay Terrace           0.024390           0.000000   
5                Bayside           0.000000           0.000000   
6              Bayswater           0.000000           0.000000   
7             Beechhurst           0.000000           0.000000   
8               Bellaire           0.000000           0.000000   
9           Belle Harbor           0.000000           0.000000   
10             Bellerose           0.000000           0.000000   
11            Blissville           0.000000           0.000000   
12          Breezy Point           0.000000           0.000000   
13             Briarwood           0.000000           0.000000   
14         Broad Channel           0.000000           0.000000   
15            Brookville           0.000000           0.000000   
16       Cambria Heights           0.000000           0.000000   
17         College Point           0.000000           0.000000   
18                Corona           0.000000           0.000000   
19            Douglaston           0.000000           0.000000   
20         East Elmhurst           0.000000           0.000000   
21              Edgemere           0.000000           0.000000   
22              Elmhurst           0.000000           0.000000   
23          Far Rockaway           0.000000           0.000000   
24           Floral Park           0.000000           0.000000   
25              Flushing           0.000000           0.000000   
26          Forest Hills           0.000000           0.000000   
27  Forest Hills Gardens           0.000000           0.000000   
28         Fresh Meadows           0.000000           0.000000   
29             Glen Oaks           0.000000           0.000000   
30              Glendale           0.000000           0.000000   
31               Hammels           0.000000           0.000000   
32             Hillcrest           0.000000           0.000000   
33                Hollis           0.000000           0.000000   
34            Holliswood           0.000000           0.000000   
35          Howard Beach           0.000000           0.000000   
36         Hunters Point           0.000000           0.000000   
37       Jackson Heights           0.000000           0.000000   
38        Jamaica Center           0.000000           0.000000   
39       Jamaica Estates           0.000000           0.000000   
40         Jamaica Hills           0.000000           0.000000   
41           Kew Gardens           0.000000           0.000000   
42     Kew Gardens Hills           0.000000           0.000000   
43             Laurelton           0.000000           0.000000   
44           Lefrak City           0.000000           0.000000   
45            Lindenwood           0.000000           0.000000   
46           Little Neck           0.000000           0.000000   
47      Long Island City           0.000000           0.000000   
48                 Malba           0.000000           0.000000   
49               Maspeth           0.000000           0.000000   
50        Middle Village           0.000000           0.000000   
51           Murray Hill           0.000000           0.000000   
52              Neponsit           0.000000           0.000000   
53          North Corona           0.000000           0.000000   
54       Oakland Gardens           0.000000           0.000000   
55            Ozone Park           0.000000           0.000000   
56               Pomonok           0.000000           0.000000   
57        Queens Village           0.000000           0.000000   
58       Queensboro Hill           0.000000           0.000000   
59          Queensbridge           0.000000           0.0000

In [29]:
len(kl_grouped[kl_grouped["Gym"] > 0])

17

<h3>CREATING A NEW DATAFRAME FOR HOTELS ONLY</h3>


In [30]:
kl_mall = kl_grouped[["city","Gym"]]
kl_mall.head()

city   Gym
0          Arverne  0.00
1          Astoria  0.02
2  Astoria Heights  0.00
3       Auburndale  0.00
4      Bay Terrace  0.00

<h3>CLUSTERING</h3>

In [32]:
kclusters = 3

kl_clustering = kl_mall.drop(["city"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(kl_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 2, 0, 0, 0, 2, 0, 1, 0, 0])

In [33]:
kl_merged = kl_mall.copy()

# add clustering labels
kl_merged["Cluster Labels"] = kmeans.labels_
kl_merged.head()

city   Gym  Cluster Labels
0          Arverne  0.00               0
1          Astoria  0.02               2
2  Astoria Heights  0.00               0
3       Auburndale  0.00               0
4      Bay Terrace  0.00               0

In [40]:
df1=pd.read_csv('Queens_venues.csv')
df1.drop(columns=['Unnamed: 0'],inplace=True)
df1.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Astoria              40.768509              -73.915654   
1      Astoria              40.768509              -73.915654   
2      Astoria              40.768509              -73.915654   
3      Astoria              40.768509              -73.915654   
4      Astoria              40.768509              -73.915654   

              Venue  Venue Latitude  Venue Longitude        Venue Category  
0      Favela Grill       40.767348       -73.917897  Brazilian Restaurant  
1    Orange Blossom       40.769856       -73.917012          Gourmet Shop  
2  Titan Foods Inc.       40.769198       -73.919253          Gourmet Shop  
3   CrossFit Queens       40.769404       -73.918977                   Gym  
4      Off The Hook       40.767200       -73.918104    Seafood Restaurant

In [41]:
kl_merged = kl_merged.join(df1.set_index("Neighborhood"), on="city")
kl_merged.head()

city  Gym  Cluster Labels  Neighborhood Latitude  \
0  Arverne  0.0               0              40.589144   
0  Arverne  0.0               0              40.589144   
0  Arverne  0.0               0              40.589144   
0  Arverne  0.0               0              40.589144   
0  Arverne  0.0               0              40.589144   

   Neighborhood Longitude                         Venue  Venue Latitude  \
0              -73.791992  Rockaway Beach - 60th Street       40.589328   
0              -73.791992            Far Rockaway Beach       40.588139   
0              -73.791992  Rockaway Beach - 69th Street       40.587350   
0              -73.791992            Locals Surf School       40.587016   
0              -73.791992           Breakwater Surf Co.       40.590795   

   Venue Longitude Venue Category  
0       -73.789144          Beach  
0       -73.795659      Surf Spot  
0       -73.797250      Surf Spot  
0       -73.796337      Surf Spot  
0       -73.796416     Board Shop

<h3>SORTING THE CLUSTERS</h3>


In [42]:
kl_merged.sort_values(["Cluster Labels"], inplace=True)
kl_merged

city       Gym  Cluster Labels  Neighborhood Latitude  \
0                Arverne  0.000000               0              40.589144   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
54       Oakland Gardens  0.000000               0              40.745619   
56               Pomonok  0.000000               0              40.734936   
58       Queensboro Hill  0.000000               0              40.744572   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
57        Queens Village  0.000000               0              40.718893   
56               Pomonok  0.000000               0              40.734936   
56               Pomonok  0.000000               0              40.734936   
56               Pomonok  0.000000               0              40.734936   
56              

In [51]:
a.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Astoria              40.768509              -73.915654   
1      Astoria              40.768509              -73.915654   
2      Astoria              40.768509              -73.915654   
3      Astoria              40.768509              -73.915654   
4      Astoria              40.768509              -73.915654   

              Venue  Venue Latitude  Venue Longitude        Venue Category  
0      Favela Grill       40.767348       -73.917897  Brazilian Restaurant  
1    Orange Blossom       40.769856       -73.917012          Gourmet Shop  
2  Titan Foods Inc.       40.769198       -73.919253          Gourmet Shop  
3   CrossFit Queens       40.769404       -73.918977                   Gym  
4      Off The Hook       40.767200       -73.918104    Seafood Restaurant

In [56]:
latit=a['Neighborhood Latitude'].mean()
latit
longit=a['Neighborhood Longitude'].mean()

In [61]:
map_clusters = folium.Map(location=[latit, longit], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
limit=1000
index=0
markers_colors = []
for lat, lon, poi, cluster in zip(kl_merged['Venue Latitude'], kl_merged['Venue Longitude'], kl_merged['city'], kl_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
    index += 1
    if index == limit:
        break
       
map_clusters
#map_clusters.save('clustermap.html')

In [47]:
kl_merged.loc[kl_merged['Cluster Labels'] == 0]

city   Gym  Cluster Labels  Neighborhood Latitude  \
0                Arverne  0.00               0              40.589144   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
54       Oakland Gardens  0.00               0              40.745619   
56               Pomonok  0.00               0              40.734936   
58       Queensboro Hill  0.00               0              40.744572   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
57        Queens Village  0.00               0              40.718893   
56               Pomonok  0.00               0              40.734936   
56               Pomonok  0.00               0              40.734936   
56               Pomonok  0.00               0              40.734936   
56               Pomonok  0.00               0              40.734936   
56               Pomonok  0.00               0              40.734936   
56               Pomonok  0.00               0              40.734936   
56   

In [44]:
kl_merged.head()

city  Gym  Cluster Labels  Neighborhood Latitude  \
0           Arverne  0.0               0              40.589144   
54  Oakland Gardens  0.0               0              40.745619   
54  Oakland Gardens  0.0               0              40.745619   
54  Oakland Gardens  0.0               0              40.745619   
54  Oakland Gardens  0.0               0              40.745619   

    Neighborhood Longitude                         Venue  Venue Latitude  \
0               -73.791992  Rockaway Beach - 60th Street       40.589328   
54              -73.754950                   Patoug Food       40.748759   
54              -73.754950     John Zangler Watch Expert       40.749247   
54              -73.754950   Red Arrow Card & Stationary       40.748499   
54              -73.754950           Dime Community Bank       40.748086   

    Venue Longitude Venue Category  
0        -73.789144          Beach  
54       -73.757744           Food  
54       -73.756252  Jewelry Store  
54       -73.756339      Gift Shop  
54       -73.756523           Bank

In [49]:
kl_merged.loc[kl_merged['Cluster Labels'] == 1]

city       Gym  Cluster Labels  Neighborhood Latitude  \
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
13            Briarwood  0.090909               1              40.710935   
26         Forest Hills  0.076923               1              40.725264   
13            Briarwood  0.090909               1              40.710935   
7            Beechhurst  0.055556               1              40.792781   
13            Briarwood  0.090909               1              40.710935   
7            Beechhurst  0.055556               1              40.792781   
7            Beechhurst  0.055556               1              40.792781   
7            Beechhurst  0.055556               1              40.792781   
7            Beechhurst  0.055556               1              40.792781   
7            Beechhurst  0.055556               1              40.792781   
7            Beechhurst  0.055556               1              40.792781   
7            Beechhurst  0.055556               1              40.792781   
13            Briarwood  0.090909               1              40.710935   
7            Beechhurst  0.055556               1              40.792781   
26         Forest Hills  0.076923               1              40.725264   
13            Briarwood  0.090909               1              40.710935   
13            Briarwood  0.090909               1              40.710935   
13            Briarwood  0.090909               1              40.710935   
13            Briarwood  0.090909               1              40.710935   
13            Briarwood  0.090909               1              40.710935   
13            Briarwood  0.090909               1              40.710935   
7            Beechhurst  0.055556               1              40.792781   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.725264   
45           Lindenwood  0.100000               1              40.663918   
45           Lindenwood  0.100000               1              40.663918   
45           Lindenwood  0.100000               1              40.663918   
45           Lindenwood  0.100000               1              40.663918   
45           Lindenwood  0.100000               1              40.663918   
45           Lindenwood  0.100000               1              40.663918   
45           Lindenwood  0.100000               1              40.663918   
45           Lindenwood  0.100000               1              40.663918   
45           Lindenwood  0.100000               1              40.663918   
45           Lindenwood  0.100000               1              40.663918   
26         Forest Hills  0.076923               1              40.725264   
26         Forest Hills  0.076923               1              40.7

In [48]:
kl_merged.loc[kl_merged['Cluster Labels'] == 2]

city       Gym  Cluster Labels  Neighborhood Latitude  \
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
36     Hunters Point  0.013514               2              40.743414   
36     Hunters Point  0.013514               2              40.743414   
36     Hunters Point  0.013514               2              40.743414   
36     Hunters Point  0.013514               2              40.743414   
5            Bayside  0.014085               2              40.766041   
36     Hunters Point  0.013514               2              40.743414   
36     Hunters Point  0.013514               2              40.743414   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
36     Hunters Point  0.013514               2              40.743414   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
38    Jamaica Center  0.023810               2              40.704657   
36     Hunters Point  0.013514               2              40.743414   
36     Hunters Point  0.013514               2              40.743414   
5            Bayside  0.014085               2              40.766041   
5            Bayside  0.014085               2              40.766041   
36     Hunters Point  0.013514               2              40.743414   
36     Hunters Point  0.013514               2              40.743414   
5

<h2> Observations</h2>

<H4>According to the observations, high number of gym already exist in the cluster 2. Moderate amount of gym exist in cluster 1 and very low amount of gym in cluster 0. Seting up a new gym in cluster 2 can be dangerous due to competetion from the existing gym. However setting up a new gym in cluster 1 & 0 can be beneficial.</H4>